In [5]:
import numpy as np
import pandas as pd

import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel

import string
import re
import spacy
from spacy.tokenizer import Tokenizer
from nltk.corpus import stopwords

import pyLDAvis
import pyLDAvis.gensim

from bs4 import BeautifulSoup

from sklearn.model_selection import train_test_split

from joblib import Parallel, delayed

In [ ]:
# ! pip install --user pyLDAvis

In [2]:
data = pd.read_csv('corpus_and_tags.csv')
data.head()

Question  \
0  How to convert Decimal to Double in C#? I want...   
1  Calculate relative time in C# Given a specific...   
2  Determine a user's timezone Is there a standar...   
3  What is the fastest way to get the value of π?...   
4  How to use the C socket API in C++ on z/OS I'm...   

                                               Tags  
0  c# floating-point type-conversion double decimal  
1      c# datetime time datediff relative-time-span  
2  html browser timezone user-agent timezone-offset  
3   performance algorithm language-agnostic unix pi  
4                       c++ c sockets mainframe zos

In [4]:
X = data['Question']
y = data['Tags']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


In [ ]:
data.info()

In [ ]:
# import nltk
# import string
# from nltk.stem import WordNetLemmatizer

# nltk.download('stopwords')
# nltk.download('punkt')
# nltk.download('words')
# nltk.download('wordnet')

In [ ]:
# !pip install -U pip setuptools wheel
# !pip install -U spacy
# !python -m spacy download en_core_web_sm

In [ ]:
# nltk.download('omw-1.4')


In [6]:
nlp = spacy.load('en_core_web_sm')
# nlp.tokenizer = Tokenizer(nlp.vocab, token_match=re.compile(r'\S+').match)
from spacy.util import compile_prefix_regex, compile_infix_regex, compile_suffix_regex

def custom_tokenizer(nlp):
    infix_re = re.compile(r'''[(\,\?\:\;\‘\’\`\“\”\"\'~]''')
    prefix_re = compile_prefix_regex(nlp.Defaults.prefixes)
    suffixes = list(nlp.Defaults.suffixes)
    suffixes.remove("#")
    suffix_re = compile_suffix_regex(suffixes)
    return Tokenizer(nlp.vocab, prefix_search=prefix_re.search,
                                suffix_search=suffix_re.search,
                                infix_finditer=infix_re.finditer,
                                token_match=None)

nlp.tokenizer = custom_tokenizer(nlp)
stopwords_list = stopwords.words('english')

def is_number(s):
    try:
        float(s)
        return True
    except ValueError:
        return False

def preprocess_doc(doc):
#     preprocess_list = []
#     for doc in listofdocs :           
#             print( token.pos_)# if token.pos_ in ['VERB','NOUN','X','PROPN']
#         tokenize_doc = gensim.utils.simple_preprocess(doc ,min_len=1)
    tokenize_doc = [token.lemma_ for token in nlp(doc) if token.pos_ in ['VERB','NOUN','X','PROPN']]
    tokenize_doc_w_punct = [token.lower() for token in tokenize_doc
                                if token not in string.punctuation]
    tokenize_doc_w_num = [token for token in tokenize_doc_w_punct
                              if not is_number(token)]
    tokenize_doc_w_longw = [token for token in tokenize_doc_w_num
                               if len(token)<=40]
    tokenize_doc_w_stopw = [token for token in tokenize_doc_w_longw
                               if token not in stopwords_list]
    tokenize_doc_w_noprint = [token for token in tokenize_doc_w_stopw
                               if token.isprintable()]

#     preprocess_list.append(tokenize_doc_w_noprint)

    return tokenize_doc_w_noprint

In [ ]:
preprocess_list_of_docs(['c++ la .la fra-nce.ko chien une \n'])

In [8]:
X_train=X_train.reset_index(drop=True)
preprocess_list = Parallel(n_jobs=22, prefer="threads")(delayed(preprocess_doc)(X_train[i]) for i in range(len(X_train)))
print('Phrase de base : '+X_train[1])
print(preprocess_list[1])

Phrase de base : How to expose std::pair to python using boost::python? How to expose std::pair to python using boost::python? When I expose for example vector<string> I simply write:
class_<std::vector<std::string> >("StringVec")
    .def(vector_indexing_suite<std::vector<std::string> >())
;

But I don't know how to deal with std::pair.

['expose', 'std', 'pair', 'python', 'use', 'boost', 'python', 'expose', 'std', 'pair', 'python', 'use', 'boost', 'python', 'expose', 'example', 'vector<stre', 'write', 'class_<std', 'vector<std', 'string', 'stringvec', 'vector_indexing_suite<std', 'vector<std', 'string', 'know', 'deal', 'std', 'pair']


In [32]:
id2word = corpora.Dictionary(preprocess_list)
print(len(id2word))
id2word.filter_extremes(no_below=10,no_above=0.2,keep_n=None)
print(len(id2word))


1190386
39701


In [33]:
# id2word = corpora.Dictionary(preprocess_list)

corpus=[]
for text in preprocess_list:
    new = id2word.doc2bow(text)
    corpus.append(new)
    
print(corpus[1])
[(id2word[id], count) for id, count in corpus[1]]

[(12, 1), (30, 2), (31, 1), (32, 1), (33, 3), (34, 3), (35, 4), (36, 3), (37, 2), (38, 2), (39, 1), (40, 1)]


[('know', 1),
 ('boost', 2),
 ('deal', 1),
 ('example', 1),
 ('expose', 3),
 ('pair', 3),
 ('python', 4),
 ('std', 3),
 ('string', 2),
 ('vector<std', 2),
 ('vector<stre', 1),
 ('write', 1)]

In [23]:
[(id2word[id], count) for id, count in corpus[1]]

[('boost', 2),
 ('class_<std', 1),
 ('expose', 3),
 ('pair', 3),
 ('stringvec', 1),
 ('vector<std', 2),
 ('vector<stre', 1),
 ('vector_indexing_suite<std', 1)]

In [ ]:
#tf-idf removal
from gensim.models import TfidfModel

tfidf = TfidfModel(corpus, id2word=id2word)
low_value = 0.2
words=[]
words_missing_in_tfidf=[]
for i in range(0,len(corpus)):
    bow = corpus[i]
    low_value_words = []
    tfidf_ids = [id for id, value in tfidf[bow]]
    bow_ids = [id for id,value in bow]
    low_value_words = [id for id,value in tfidf[bow] if value < low_value]
#     drops = low_value_words+words_missing_in_tfidf
#     for items in drops:
#         words.append(id2word[item])
    words_missing_in_tfidf = [id for id in bow_ids if id not in tfidf_ids]
    new_bow = [b for b in bow if b[0] not in low_value_words and b[0] not in words_missing_in_tfidf]
    corpus[i] = new_bow

In [ ]:
corpus[1001]

In [ ]:
import tqdm


In [ ]:
corpus

In [ ]:
from collections.abc import Iterable
isinstance(corpus, Iterable)

In [ ]:
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

In [34]:
lda_model = gensim.models.ldamulticore.LdaMulticore(corpus=corpus,
                                           id2word=id2word,
                                            workers=11,
                                           num_topics=300,
                                           random_state=100,
                                           chunksize=100,
                                           passes=5,)

In [ ]:
def extract_topics_keywords(ldamodel, corpus):
    # Init output
    sent_topics_df = pd.DataFrame()
    # Get main topic in each document
    for i, row in enumerate(ldamodel[corpus]):
        row = sorted(row, key=lambda x: (x[1]), reverse=True)
        # Get the Dominant topic, Perc Contribution and Keywords for each document
        for j, (topic_num, prop_topic) in enumerate(row):
            if j == 0:  # => dominant topic
                wp = ldamodel.show_topic(topic_num)
                topic_keywords = " ".join([word for word, prop in wp[0:5]])
                results = {'Dominant_Topic':topic_num,
                           'Perc_Contribution':round(prop_topic,4),
                           'Topic_Keywords':topic_keywords
                          }
                sent_topics_df = pd.concat([sent_topics_df, pd.DataFrame([results])], ignore_index=True)
            else:
                break

    return(sent_topics_df)

topics_df = extract_topics_keywords(ldamodel=lda_model, corpus=corpus)
topics_df = pd.concat([topics_df, data['Tags'][0:10000]], axis=1)
topics_df

In [ ]:
tt=sorted(lda_model.get_document_topics(corpus[0]), key=lambda x: (x[1]), reverse=True)
lda_model.show_topic(tt[0][0])

In [ ]:
lda_model.get_document_topics(corpus[1])


In [ ]:
corpus[1]

In [40]:
def extract_topics_keywords(ldamodel, corpus):
    # Init output
    sent_topics_df = pd.DataFrame()
    # Get main topic in each document
    for bow in corpus:
        topics_sorted = sorted(ldamodel.get_document_topics(bow), key=lambda x: (x[1]), reverse=True)
        # Get the Dominant topic, Perc Contribution and Keywords for each document
        if topics_sorted:
            wp = ldamodel.show_topic(topics_sorted[0][0])
            topic_keywords = " ".join([word for word, prop in wp[0:5]])
            results = {'Dominant_Topic':topics_sorted[0][0],
                           'Perc_Contribution':round(topics_sorted[0][1],4),
                           'Topic_Keywords':topic_keywords
                          }
            sent_topics_df = pd.concat([sent_topics_df, pd.DataFrame([results])], ignore_index=True)
        else:
            results = {'Dominant_Topic':np.Nan,
                           'Perc_Contribution':np.Nan,
                           'Topic_Keywords':np.Nan
                          }
            sent_topics_df = pd.concat([sent_topics_df, pd.DataFrame([results])], ignore_index=True)
    return(sent_topics_df)

# topics_df = extract_topics_keywords(ldamodel=lda_model, corpus=corpus)
# topics_df = pd.concat([topics_df, data['Tags'][0:10000]], axis=1)
# topics_df

In [ ]:
topics_df[7604:7750]

In [36]:
X_test=X_test.reset_index(drop=True)
X_test_preprocessed = Parallel(n_jobs=22, prefer="threads")(delayed(preprocess_doc)(X_test[i]) for i in range(len(X_test)))
print('Phrase de base : '+X_test[1])
print(X_test_preprocessed[1])

corpus_test=[]
for text in X_test_preprocessed:
    new = id2word.doc2bow(text)
    corpus_test.append(new)
    
print(corpus_test[1])
[(id2word[id], count) for id, count in corpus_test[1]]

Phrase de base : Conditional unique constraint with multiple fields in oracle db I have this table:
XPTO_TABLE (id, obj_x, date_x, type_x, status_x)

I wanna create a unique constraint that applies to the fields (obj_x, date_x, type_x) only when status_x <> 5.
I have tried to create this one but Oracle says:
line 1: ORA-00907: missing right parenthesis

CREATE UNIQUE INDEX UN_OBJ_DT_TYPE_STATUS
ON XPTO_TABLE(
    (CASE
         WHEN STATUS_X <> 5
         THEN
             (OBJ_X,
              TO_CHAR (DATE_X, 'dd/MM/yyyy'),
              TYPE_X)
         ELSE
             NULL
     END));

What's the correct syntax ?

['constraint', 'field', 'oracle', 'db', 'table', 'obj_x', 'date_x', 'wanna', 'create', 'constraint', 'apply', 'field', 'obj_x', 'date_x', 'try', 'create', 'oracle', 'say', 'line', 'ora-00907', 'miss', 'parenthesis', 'create', 'unique', 'index', 'xpto_table', 'case', 'obj_x', 'to_char', 'date_x', 'dd/mm/yyyy', 'type_x', 'else', 'null', 'end', 'syntax']
[(7, 2), (21, 1), 

[('constraint', 2),
 ('say', 1),
 ('end', 1),
 ('index', 1),
 ('case', 1),
 ('null', 1),
 ('table', 1),
 ('unique', 1),
 ('line', 1),
 ('db', 1),
 ('apply', 1),
 ('field', 2),
 ('miss', 1),
 ('syntax', 1),
 ('parenthesis', 1),
 ('oracle', 2),
 ('to_char', 1),
 ('else', 1),
 ('dd/mm/yyyy', 1),
 ('wanna', 1)]

In [42]:
topics_df = extract_topics_keywords(ldamodel=lda_model, corpus=corpus_test)
# topics_df = pd.concat([topics_df, y_test], axis=1,ignore_index = True)
topics_df

Dominant_Topic  Perc_Contribution  \
0                  60             0.1965   
1                 189             0.1399   
2                 218             0.1428   
3                 114             0.2017   
4                 277             0.2116   
...               ...                ...   
44296             277             0.2157   
44297             110             0.2142   
44298              59             0.1317   
44299             274             0.3064   
44300             122             0.1481   

                                       Topic_Keywords  
0                                 integer bit n j max  
1                     field column rate equivalent eg  
2                      array search label icon escape  
3                 page content counter helper user_id  
4                 learn question know tutorial apache  
...                                               ...  
44296             learn question know tutorial apache  
44297                     test unit expect fail write  
44298          import module package class processing  
44299  cell description tableview uitableview section  
44300                         memory usage mb gb disk  

[44301 rows x 3 columns]

In [59]:
topics_df = pd.concat([topics_df, y_test.to_frame().reset_index(drop=True)],ignore_index=False,axis=1)
topics_df

Dominant_Topic  Perc_Contribution  \
0                  60             0.1965   
1                 189             0.1399   
2                 218             0.1428   
3                 114             0.2017   
4                 277             0.2116   
...               ...                ...   
44296             277             0.2157   
44297             110             0.2142   
44298              59             0.1317   
44299             274             0.3064   
44300             122             0.1481   

                                       Topic_Keywords  \
0                                 integer bit n j max   
1                     field column rate equivalent eg   
2                      array search label icon escape   
3                 page content counter helper user_id   
4                 learn question know tutorial apache   
...                                               ...   
44296             learn question know tutorial apache   
44297                     test unit expect fail write   
44298          import module package class processing   
44299  cell description tableview uitableview section   
44300                         memory usage mb gb disk   

                                                    Tags  
0                 java recursion lambda java-8 fibonacci  
1      sql oracle conditional-statements unique uniqu...  
2        powershell escaping character unc select-string  
3      iphone ios image-processing uiimagepickercontr...  
4      javascript model-view-controller web-applicati...  
...                                                  ...  
44296  javascript node.js proxy websocket push-notifi...  
44297                    c# unit-testing mocking tdd moq  
44298  java spring spring-mvc spring-boot spring-data...  
44299  php wordpress woocommerce product hook-woocomm...  
44300    django performance concurrency apache2 mod-wsgi  

[44301 rows x 4 columns]

In [61]:
from simphile import jaccard_list_similarity
l=[]
for i in range(len(topics_df[0:1000])):
    l.append(jaccard_list_similarity(topics_df['Topic_Keywords'][i].split(), topics_df['Tags'][i].split()))
np.mean(l)

0.027777777777777776

In [35]:
pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim.prepare(lda_model,corpus, id2word, mds='mmds', R=30)
vis

C:\Users\yodlaf\AppData\Roaming\Python\Python39\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(
C:\Users\yodlaf\AppData\Roaming\Python\Python39\site-packages\sklearn\manifold\_mds.py:299: FutureWarning: The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.
  warnings.warn(


PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
140   -0.013331 -0.408466       1        1  1.254845
26     0.406237 -0.191336       2        1  1.240329
265   -0.399088 -0.041221       3        1  1.095969
277   -0.028753  0.017313       4        1  1.050658
27     0.073326  0.096982       5        1  0.989412
...         ...       ...     ...      ...       ...
184    0.350867  0.364920     296        1  0.075289
290    0.292856 -0.267325     297        1  0.073079
107   -0.104542 -0.495795     298        1  0.072376
67    -0.560921 -0.039025     299        1  0.069993
228    0.525147  0.066385     300        1  0.061106

[300 rows x 5 columns], topic_info=             Term          Freq         Total  Category  logprob  loglift
433        import  65837.000000  65837.000000   Default  30.0000  30.0000
445         value  65111.000000  65111.000000   Default  29.0000  29.0000
37         string  86635.000000  86635.000000   Default  28.0000  28.0000
292          test  57875.000000  57875.000000   Default  27.0000  27.0000
257           int  63096.000000  63096.000000   Default  26.0000  26.0000
...           ...           ...           ...       ...      ...      ...
12127  headername     46.708618     49.318374  Topic300  -5.1385   7.3460
2565       darwin    198.259820    258.658406  Topic300  -3.6928   7.1344
2569     optional     80.709432    636.978740  Topic300  -4.5916   5.3344
168        finish     44.059141   4912.527746  Topic300  -5.1969   2.6863
2506          x64     41.455196   1346.260293  Topic300  -5.2578   3.9199

[14248 rows x 6 columns], token_table=       Topic      Freq         Term
term                               
16045     97  0.973310      #ff0000
16519    268  0.983558         #fff
8221      69  0.977674  #mycarousel
8339     162  0.023094           $1
8339     203  0.923760           $1
...      ...       ...          ...
15272    299  0.985809            ╬
17247    262  0.993399            ✓
830      234  0.987574            ✗
13473    229  0.988587            ️
14978    252  0.999278            �

[77131 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[141, 27, 266, 278, 28, 162, 152, 245, 211, 242, 151, 139, 286, 33, 235, 164, 194, 111, 253, 171, 94, 181, 72, 70, 60, 6, 96, 203, 123, 297, 244, 241, 26, 64, 225, 260, 172, 147, 243, 289, 227, 32, 251, 277, 280, 2, 124, 126, 88, 175, 52, 219, 83, 174, 49, 201, 113, 246, 193, 61, 295, 160, 215, 65, 51, 78, 221, 249, 53, 58, 218, 287, 166, 206, 38, 115, 154, 54, 214, 279, 71, 177, 107, 63, 205, 190, 176, 44, 14, 69, 262, 294, 272, 79, 13, 168, 156, 20, 25, 149, 212, 232, 292, 209, 142, 155, 39, 47, 269, 202, 133, 74, 98, 34, 271, 263, 276, 192, 80, 136, 165, 8, 73, 77, 180, 106, 183, 299, 273, 284, 226, 100, 84, 191, 169, 224, 45, 128, 130, 196, 199, 144, 267, 101, 105, 22, 36, 29, 298, 46, 76, 258, 81, 189, 95, 140, 66, 261, 122, 150, 121, 275, 256, 187, 184, 233, 10, 75, 118, 57, 240, 288, 182, 3, 17, 204, 145, 59, 296, 264, 223, 12, 19, 92, 43, 48, 195, 213, 7, 274, 167, 129, 89, 230, 5, 282, 87, 281, 99, 104, 239, 56, 15, 23, 270, 127, 138, 31, 161, 103, 21, 135, 112, 143, 119, 208, 188, 16, 179, 4, 293, 120, 268, 234, 186, 163, 222, 24, 159, 254, 283, 285, 197, 1, 252, 90, 236, 109, 85, 137, 259, 125, 117, 210, 231, 198, 102, 237, 238, 255, 41, 42, 207, 30, 200, 91, 116, 11, 257, 290, 216, 153, 62, 86, 37, 50, 131, 265, 67, 250, 146, 9, 93, 40, 114, 217, 132, 110, 157, 35, 173, 97, 247, 134, 228, 55, 300, 170, 18, 248, 82, 158, 148, 178, 220, 185, 291, 108, 68, 229])